In [40]:
import sys
import os
import torch
import torch.nn as nn
import matplotlib.pyplot as plt

rootdir = os.path.abspath(sys.path[0] + '/../')
sys.path.append(rootdir)
torch.cuda.set_device(0)
print("Set CUDA:%d as current device." % torch.cuda.current_device())
torch.autograd.set_grad_enabled(False)

from data.spherical_view_syn import *
from configs.spherical_view_syn import SphericalViewSynConfig
from utils import netio
from utils import img
from utils import device
from utils.view import *
from components.fnr import FoveatedNeuralRenderer


def load_net(path):
    config = SphericalViewSynConfig()
    config.from_id(os.path.splitext(path)[0])
    config.sa['perturb_sample'] = False
    net = config.create_net().to(device.default())
    netio.load(path, net)
    return net


def find_file(prefix):
    for path in os.listdir():
        if path.startswith(prefix):
            return path
    return None


def plot_images(images):
    plt.figure(figsize=(12, 4))
    plt.subplot(131)
    img.plot(images['layers_img'][0])
    plt.subplot(132)
    img.plot(images['layers_img'][1])
    plt.subplot(133)
    img.plot(images['layers_img'][2])
    #plt.figure(figsize=(12, 12))
    #img.plot(images['overlaid'])
    #plt.figure(figsize=(12, 12))
    #img.plot(images['blended_raw'])
    plt.figure(figsize=(12, 12))
    img.plot(images['blended'])


scenes = {
    'classroom': 'classroom_all',
    'stones': 'stones_all',
    'barbershop': 'barbershop_all',
    'lobby': 'lobby_all'
}

fov_list = [20, 45, 110]
res_list = [(256, 256), (256, 256), (256, 230)]
res_full = (1600, 1440)

Set CUDA:0 as current device.


In [59]:
scene = 'classroom'
os.chdir(f'{rootdir}/data/__new/{scenes[scene]}')
print('Change working directory to ', os.getcwd())

fovea_net = load_net(find_file('fovea'))
periph_net = load_net(find_file('periph'))
renderer = FoveatedNeuralRenderer(fov_list, res_list, nn.ModuleList([fovea_net, periph_net, periph_net]),
                                  res_full, device=device.default())

Change working directory to  /home/dengnc/dvs/data/__new/classroom_all
Load net from fovea200@snerffast4-rgb_e6_fc512x4_d1.00-7.00_s64_~p.pth ...
Load net from periph200@snerffast2-rgb_e6_fc256x4_d1.00-7.00_s32_~p.pth ...


In [61]:
params = {
    'classroom': [
        [0, 0, 0,   0, 0,   0, 0], #For demo with nerf
        [0, 0, 0,   20, -20,   0, 0], #For demo with nerf
        #[0, 0, 0,   -53, 0,   0, 0],
        [0.3, 0, 0.3, 0, 0], # For panorama (Trans)
        [-0.3, -0.3, -0.3, 0, 0], # For panorama (Trans)
        [0, -0.3, 0.3, 0, 10], # For panorama (V-D)
        [0, 0.3, 0.3, 0, 10], # For panorama (V-D)
        [0, 0, 0,   10, -13,   0, 0], # For fig latency-quality
    ],
    'stones': [
        #[0, 0, 0, 0, 10, -300, -50],
        #[0, 0, 0, 0, 10, 200, -50]
        [-0.5, -0.5, -0.5, -25, 0, 50, -230], #For demo with nerf
        [-0.5, -0.5, -0.5, 0, 0, 280, -220], #For demo with nerf
    ],
    'barbershop': [
        #[0, 0, 0,   0, 0,   0, 0],
        [0, 0, 0,   20, 10,   0, 0], #For demo with nerf
        [0, 0, 0,   -20, -10,   0, 0], #For demo with nerf
        [0, 0, 0, 20, 0, -300, 50], #For fig rendering-system
        #[0, 0, 0, -140, -30, 150, -250],
        #[0, 0, 0, -60, -30, 75, -125],
        [0.15, 0, 0.15,   -13, -5,   0, 0], #For panorama (Trans) / Teaser
        [-0.15, -0.15, 0, 12, 12, 0, 0], #For panorama (Trans) / Teaser
    ],
    'lobby': [
        #[0, 0, 0, 0, 0, 75, 0],
        #[0, 0, 0, 0, 0, 5, 150],
        #[0, 0, 0, -120, 0, 75, 50],
        [0, 0, 0, 0, 0, 0, 0],
        [-0.5, -0.5, -0.5, -25, 0, -150, 0],
        [-0.5, -0.5, -0.5, 25, 25, -150, 200],
    ]
}

for i, param in enumerate(params[scene]):
    view = Trans(torch.tensor(param[:3], device=device.default()),
                 torch.tensor(euler_to_matrix([-param[4], param[3], 0]), device=device.default()).view(3, 3))
    images = renderer(view, param[-2:], using_mask=False, ret_raw=True)
    images['overlaid'] = renderer.foveation.synthesis(images['layers_raw'], param[-2:], do_blend=False)
    if True:
        outputdir = '../__demo/mono/'
        os.makedirs(outputdir, exist_ok=True)
        img.save(images['layers_img'][0], f'{outputdir}{scene}_{i}_fovea.png')
        img.save(images['layers_img'][1], f'{outputdir}{scene}_{i}_mid.png')
        img.save(images['layers_img'][2], f'{outputdir}{scene}_{i}_periph.png')
        img.save(images['blended'], f'{outputdir}{scene}_{i}_blended.png')
        #img.save(images['overlaid'], f'{outputdir}{scene}_{i}_overlaid.png')
        #img.save(images['blended_raw'], f'{outputdir}{scene}_{i}_blended_raw.png')
    else:
        images = plot_images(images)


In [3]:
def load_views(data_desc_file) -> Trans:
    with open(data_desc_file, 'r', encoding='utf-8') as file:
        data_desc = json.loads(file.read())
        view_centers = torch.tensor(
            data_desc['view_centers'], device=device.default()).view(-1, 3)
        view_rots = torch.tensor(
            data_desc['view_rots'], device=device.default()).view(-1, 3, 3)
        return Trans(view_centers, view_rots)


views = load_views('nerf_cvt.json')
print('Dataset loaded.')
for view_idx in range(views.size()[0]):
    center = (0, 0)
    images = renderer(views.get(view_idx), center, using_mask=True)
    outputdir = 'nerf_our'
    os.makedirs(outputdir, exist_ok=True)
    img.save(images['blended'], f'{outputdir}/{view_idx:04d}.png')

Dataset loaded.
